# Face detection and recognition training pipeline

The following example illustrates how to fine-tune an InceptionResnetV1 model on your own dataset. This will mostly follow standard pytorch training patterns.

In [1]:
from facenet_pytorch import MTCNN, InceptionResnetV1, fixed_image_standardization, training
import torch
from torch.utils.data import DataLoader, SubsetRandomSampler
from torch import optim
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter
from torchvision import datasets, transforms
import numpy as np
import os
import pandas as pd
import glob 
from PIL import Image
import matplotlib.pyplot as plt
from IPython.display import display
import re
from collections import defaultdict

/home/obasit/50024/kaggle/kaggle_env/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-04-04 23:33:15.019806: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-04-04 23:33:15.718392: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


#### Define run parameters

The dataset should follow the VGGFace2/ImageNet-style directory layout. Modify `data_dir` to the location of the dataset on wish to finetune on.

In [2]:
data_dir = '/export2/obasit/50024/kaggle_data/train/train_mtcnn'

batch_size = 128
workers = 24

#### Determine if an nvidia GPU is available

In [3]:
device = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu')
# device = torch.device('cpu')
print('Running on device: {}'.format(device))

Running on device: cuda:1


#### Define MTCNN module

See `help(MTCNN)` for more details.

In [7]:
mtcnn = MTCNN(
    image_size=160, margin=40, min_face_size=40,
    thresholds=[0.6, 0.7, 0.7], factor=0.709, post_process=True,
    device=device, select_largest=False,
    selection_method='largest_over_threshold', keep_all=True
)

#### Perfom MTCNN facial detection

Iterate through the DataLoader object and obtain cropped faces.

In [8]:
def filter_RGB(image):
    if image.mode != 'RGB':
        image = image.convert('RGB')
    return image

class FilterRGB(object):
    def __call__(self, img):
        filtered_img = filter_RGB(img)
        if filtered_img is None:
            return None
        return filtered_img
    
transform = transforms.Compose([
    transforms.Resize((512, 512)),
    FilterRGB(),
])

dataset = datasets.ImageFolder(data_dir, transform=transform)
class_to_idx = {class_name: idx for idx, class_name in enumerate(dataset.classes)}
idx_to_class = {idx: class_name for class_name, idx in class_to_idx.items()}
dataset.samples = [
    (p, p.replace(data_dir, data_dir + '_inlcuding_grey_512_20_smallest_face_prob_90_single_faces'))
        for p, _ in dataset.samples
]
        
loader = DataLoader(
    dataset,
    num_workers=workers,
    batch_size=batch_size,
    collate_fn=training.collate_pil
)

    
for i, (x, y) in enumerate(loader):
    mtcnn(x, save_path=y)
    print('\rBatch {} of {}'.format(i + 1, len(loader)), end='')
    
# Remove mtcnn to reduce GPU memory usage
del mtcnn






/home/obasit/50024/kaggle/kaggle_env/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(


Batch 6 of 544

/home/obasit/50024/kaggle/kaggle_env/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(


Batch 68 of 544

/home/obasit/50024/kaggle/kaggle_env/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(


...

Batch 211 of 544

/home/obasit/50024/kaggle/kaggle_env/lib/python3.11/site-packages/PIL/Image.py:981: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(


Batch 467 of 544

/home/obasit/50024/kaggle/kaggle_env/lib/python3.11/site-packages/PIL/TiffImagePlugin.py:870: UserWarning: Truncated File Read
  warnings.warn(str(msg))


Batch 544 of 544

In [9]:
def delete_images_with_second_digit(folder_path):
    # Regular expression to match files with an underscore followed by a digit
    pattern = re.compile(r'\d+_\d+\.jpg')

    # Dictionary to store base filenames without second digits
    base_filenames = defaultdict(list)

    # Set to keep track of base filenames with second digit files
    base_filenames_with_second_digit = set()

    # Walk through the directory tree
    for root, dirs, files in os.walk(folder_path):
        for file_name in files:
            # Check if the file matches the pattern
            if pattern.match(file_name):
                # Extract the base filename (without the second digit)
                base_filename = re.sub(r'_(\d+)\.jpg', r'.jpg', file_name)
                base_filenames[base_filename].append(os.path.join(root, file_name))
                base_filenames_with_second_digit.add(base_filename)

    # Iterate through base filenames
    for base_filename, second_digit_files in base_filenames.items():
        # If there are files with second digits
        if base_filename in base_filenames_with_second_digit:
            # Delete all files with second digits
            for file_path in second_digit_files:
                os.remove(file_path)
                print(f"Deleted {file_path}")

            # Also delete the corresponding single digit file if it exists
            single_digit_file_path = os.path.join(folder_path, base_filename)
            if os.path.exists(single_digit_file_path):
                os.remove(single_digit_file_path)
                print(f"Deleted {single_digit_file_path}")

delete_images_with_second_digit('/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces')

Deleted /home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/28965_2.jpg
Deleted /home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/33910_2.jpg
Deleted /home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/33910_3.jpg
Deleted /home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/16190_2.jpg
Deleted /home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/63473_3.jpg
Deleted /home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/63473_4.jpg
Dele

In [10]:
with open('dump.txt', 'r') as file:
    lines = file.readlines()
# print(lines[1])
# Extract just the paths from the lines
paths = [line.split(' ')[1].strip() for line in lines]

pattern = re.compile(r'/([^/]+)$')

# Process each path
for path in paths:
    # Extract the filename from the path
    filename_match = re.search(pattern, path)
    if filename_match:
        filename = filename_match.group(1)
        # Replace the last "_number.jpg" with ".jpg"
        new_filename = re.sub(r'_\d+\.jpg$', '.jpg', filename)
        # Replace the filename in the path
        new_path = path[:-len(filename)] + new_filename
        
        print(new_path)
        try:
            os.remove(new_path)
        except:
            continue

/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/28965.jpg
/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/33910.jpg
/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/33910.jpg
/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/16190.jpg
/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/63473.jpg
/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/train_mtcnn_inlcuding_grey_512_20_smallest_face_prob_90_single_faces/Audrey_Hepburn/63473.jpg
/home/obasit/50024/kaggle/data/export2_data/kaggle_data/train/tr